### Import Python packages


In [1]:
! uv pip install E:\Work\ruzt\msyrs --upgrade

Using Python 3.12.4 environment at: E:\Work\ruzt\msyrs\.venv
Resolved 34 packages in 121ms
   Building msyrs @ file:///E:/Work/ruzt/msyrs
      Built msyrs @ file:///E:/Work/ruzt/msyrs
Prepared 1 package in 14.72s
Uninstalled 1 package in 4ms
         If the cache and target directories are on different filesystems, hardlinking may not be supported.
         If this is intentional, set `export UV_LINK_MODE=copy` or use `--link-mode=copy` to suppress this warning.
Installed 1 package in 30ms
 ~ msyrs==0.0.1 (from file:///E:/Work/ruzt/msyrs)


In [2]:
import macrosynergy
import pandas as pd
import numpy as np
import polars as pl
import os

from macrosynergy.panel import view_timelines
from macrosynergy.management.types import QuantamentalDataFrame


### Import Python bindings - `msyrs`


In [3]:
import msyrs

In [4]:
DATA_FOLDER_PATH = "E:/Work/jpmaqs-data"
# DATA_FOLDER_PATH = "C:/Users/PalashTyagi/Code/go-dataquery/jpmaqs-data"
DQ_CLIENT_ID = os.getenv("DQ_CLIENT_ID")
DQ_CLIENT_SECRET = os.getenv("DQ_CLIENT_SECRET")

In [5]:
import time

nb_start_time = time.time()

In [6]:
dfpath = f"{DATA_FOLDER_PATH}/data/ADPEMPL_SA_P1M1ML1/USD_ADPEMPL_SA_P1M1ML1.csv"

starttime = time.time()
ldf: pl.DataFrame = msyrs.qdf.load_qdf(dfpath)
print(f"Time taken to load qdf: {time.time() - starttime}")
ldf.head(5)

Time taken to load qdf: 0.004000425338745117


shape: (5, 7)
┌────────────┬─────┬────────────────────┬───────────┬─────────┬─────────┬─────────┐
│ real_date  ┆ cid ┆ xcat               ┆ value     ┆ grading ┆ eop_lag ┆ mop_lag │
│ ---        ┆ --- ┆ ---                ┆ ---       ┆ ---     ┆ ---     ┆ ---     │
│ date       ┆ str ┆ str                ┆ f64       ┆ f64     ┆ i64     ┆ i64     │
╞════════════╪═════╪════════════════════╪═══════════╪═════════╪═════════╪═════════╡
│ 2010-03-03 ┆ USD ┆ ADPEMPL_SA_P1M1ML1 ┆ -0.173806 ┆ 3.0     ┆ 3       ┆ 33      │
│ 2010-03-04 ┆ USD ┆ ADPEMPL_SA_P1M1ML1 ┆ -0.173806 ┆ 3.0     ┆ 4       ┆ 34      │
│ 2010-03-05 ┆ USD ┆ ADPEMPL_SA_P1M1ML1 ┆ -0.173806 ┆ 3.0     ┆ 5       ┆ 35      │
│ 2010-03-08 ┆ USD ┆ ADPEMPL_SA_P1M1ML1 ┆ -0.173806 ┆ 3.0     ┆ 8       ┆ 38      │
│ 2010-03-09 ┆ USD ┆ ADPEMPL_SA_P1M1ML1 ┆ -0.173806 ┆ 3.0     ┆ 9       ┆ 39      │
└────────────┴─────┴────────────────────┴───────────┴─────────┴─────────┴─────────┘

In [7]:
cids_dm = "AUD.CAD.CHF.EUR.GBP.JPY.NOK.NZD.SEK.USD".split(".")
cids_em = "CLP.COP.CZK.HUF.IDR.ILS.INR.KRW.MXN.PLN.THB.TRY.TWD.ZAR".split(".")
cids = cids_dm + cids_em
cids_dux = list(set(cids) - set(["IDR", "NZD"]))
ecos = "CPIC_SA_P1M1ML12.CPIC_SJA_P3M3ML3AR.CPIC_SJA_P6M6ML6AR.CPIH_SA_P1M1ML12.CPIH_SJA_P3M3ML3AR.CPIH_SJA_P6M6ML6AR.INFTEFF_NSA.INTRGDP_NSA_P1M1ML12_3MMA.INTRGDPv5Y_NSA_P1M1ML12_3MMA.PCREDITGDP_SJA_D1M1ML12.RGDP_SA_P1Q1QL4_20QMA.RYLDIRS02Y_NSA.RYLDIRS05Y_NSA.PCREDITBN_SJA_P1M1ML12".split(
    "."
)


mkts = "DU02YXR_NSA.DU05YXR_NSA.DU02YXR_VT10.DU05YXR_VT10.EQXR_NSA.EQXR_VT10.FXXR_NSA.FXXR_VT10.FXCRR_NSA.FXTARGETED_NSA.FXUNTRADABLE_NSA".split(
    "."
)
xcats = ecos + mkts

tickers = [f"{c}_{x}" for c in cids for x in xcats]

In [8]:
starttime = time.time()

big_df: pl.DataFrame = msyrs.qdf.load_qdf_from_download_bank(
    folder_path=DATA_FOLDER_PATH,
    xcats=xcats,
)
print(f"Time taken to load qdf batch: {time.time() - starttime}")


Time taken to load qdf batch: 1.3058679103851318


In [9]:
big_df.estimated_size("mb")

286.69339656829834

In [10]:
sel_cids = ["USD", "EUR", "GBP", "AUD", "CAD"]
start = "1990-01-01"

In [11]:
fx_xcats = [xc for xc in xcats if xc.startswith("FX")]
eq_xcats = [xc for xc in xcats if xc.startswith("EQ")]
starttime = time.time()

eq_df = msyrs.qdf.reduce_dataframe(
    df=big_df,
    cids=sel_cids,
    xcats=fx_xcats + eq_xcats,
    start=start,
)

fx_df = msyrs.qdf.reduce_dataframe(
    df=big_df, cids=sel_cids, start=start, xcats=fx_xcats, intersect=True
)
new_df: pl.DataFrame = msyrs.qdf.update_dataframe(df=eq_df, df_add=fx_df)

print(f"Time taken to reduce qdf: {time.time() - starttime}")


Time taken to reduce qdf: 0.9705278873443604


In [12]:
end_time = time.time()
print(f"Time taken: {end_time - nb_start_time} seconds")

Time taken: 2.3365907669067383 seconds


In [13]:
_cids = ["USD", "CAD"]
mx = macrosynergy.panel.linear_composite(
    df=new_df.to_pandas(),
    xcats=["EQXR_NSA", "FXXR_NSA"], 
    cids=_cids,
    weights=None,
    signs=None,
    normalize_weights=False,
    start=None,
    end=None,
    blacklist=None,
    complete_xcats=False,
    complete_cids=False,
    new_xcat="COMPOSITE",
    new_cid="GLB",
)
# view_timelines(QuantamentalDataFrame(mx), cids=_cids)

e:\Work\ruzt\msyrs\.venv\Lib\site-packages\macrosynergy\panel\linear_composite.py:437: UserWarning: USD does not have complete xcat data for ['FXXR_NSA']. These will be filled with NaNs for the calculation.
  warnings.warn(wrn_msg.format(cidx=cidx, missing_xcats=missing_xcats))


In [14]:
_cids = ["USD", "CAD"]
x = msyrs.panel.linear_composite(
    df=new_df,
    xcats=["EQXR_NSA", "FXXR_NSA"],
    cids=_cids,
    weights=None,
    signs=None,
    weight_xcats=None,
    normalize_weights=False,
    start=None,
    end=None,
    blacklist=None,
    complete_xcats=False,
    complete_cids=False,
    new_xcat="COMPOSITE",
    new_cid="GLB",
)
# view_timelines(QuantamentalDataFrame(x.to_pandas()), cids=_cids)

In [15]:
mwide = QuantamentalDataFrame(mx).to_wide().sort_index()
rwide = QuantamentalDataFrame(x.to_pandas()).to_wide().sort_index()
np.allclose((mwide - rwide).sum(axis=1), 0)

True

In [16]:
_cids = ["USD", "CAD", "EUR", "AUD"]
_xcats = ["EQXR_NSA", "FXXR_NSA"]

mx = macrosynergy.panel.linear_composite(
    df=new_df.to_pandas(),
    xcats=_xcats,
    cids=_cids,
    weights=[1, 9],
    normalize_weights=False,
    new_xcat="COMPOSITE",
    new_cid="GLB",
)
x = msyrs.panel.linear_composite(
    df=new_df,
    xcats=_xcats,
    cids=_cids,
    weights=[1, 9],
    normalize_weights=False,
    new_xcat="COMPOSITE",
    new_cid="GLB",
)
mwide = QuantamentalDataFrame(mx).to_wide().sort_index()
rwide = QuantamentalDataFrame(x.to_pandas()).to_wide().sort_index()
np.allclose((mwide - rwide).sum(axis=1), 0)

e:\Work\ruzt\msyrs\.venv\Lib\site-packages\macrosynergy\panel\linear_composite.py:437: UserWarning: USD does not have complete xcat data for ['FXXR_NSA']. These will be filled with NaNs for the calculation.
  warnings.warn(wrn_msg.format(cidx=cidx, missing_xcats=missing_xcats))


True

In [17]:

x = msyrs.panel.linear_composite(
    df=new_df,
    xcats=_xcats,
    cids=_cids,
    weights=[1, 9],
    normalize_weights=True,
    new_xcat="COMPOSITE",
    new_cid="GLB",
)
x.to_pandas().dropna(how="any")

Empty DataFrame
Columns: [real_date, value, cid, xcat]
Index: []